<h1><center>The FUDGE translation of the TENDL-2021 library from ENDF-6 to GNDS</center></h1>
<h3><center>Godfree Gert</center></h3>
<h5><center>May 24, 2023</center></h5>
<br>

**LLNL-PRES-849740**

*This work was performed under the auspices of the U.S. Department of Energy by Lawrence Livermore National Laboratory under contract DE- AC52-07NA27344. Lawrence Livermore National Security, LLC*

# Overview

- Demonstrate FUDGE installation from GitHub

- Demonstrate translation of TENDL-2021 library from ENDF6 to GNDS

- Summary of TENDL-2021 library translation from ENDF6 to GNDS

# Downloading TENDL-2021 Library

In [ ]:
%%bash

for projectile in a d g h n p t; do
  tarFile=TENDL-${projectile}.tgz
  if [[ ! -f $tarFile ]]; then
    echo https://tendl.web.psi.ch/tendl_2021/tar_files/TENDL-${projectile}.tgz
    wget https://tendl.web.psi.ch/tendl_2021/tar_files/TENDL-${projectile}.tgz
  fi
done

# FUDGE installation from GitHub

The following code demonstrates the installation of FUDGE to a Python virtual environment.

In [ ]:
%%bash

python3 -m pip install git+https://github.com/LLNL/fudge.git@6.2.0

# Translating TENDL-2021 Library from ENDF6 to GNDS

### Function to run shell commands from within python

In [17]:
import pathlib
import subprocess

def runShellCommand(commandList, cwd=pathlib.Path()):
  process = subprocess.Popen(commandList, universal_newlines=True, cwd=cwd)
  process.communicate()

### Path to FUDGE translation script

In [ ]:
import brownies

translationScript = pathlib.Path(brownies.__path__._path[0]) / 'bin' / 'endf2gnds.py'

### Arguments available in processing script

In [20]:
runShellCommand(['python3', translationScript, '-h'])

usage: endf2gnds.py [-h] [-v] [--skipBadData] [--skipCovariances]
                    [--verboseWarnings] [--printBadNK14]
                    [--continuumSpectraFix] [--ignoreBadDate]
                    [--acceptBadMF10FissionZAP] [--traceback]
                    [--formatVersion {1.10,2.0}] [--energyUnit ENERGYUNIT]
                    [--JENDL_stylePrimarygammas]
                    [--IDs {familiar,nucleus,nuclide}]
                    inFile [outputFile]

Translates an ENDF file to the GNDS format.

positional arguments:
  inFile                input file
  outputFile            output file

options:
  -h, --help            show this help message and exit
  -v, --verbose         enable verbose output. The more the gabbier.
  --skipBadData         skip bad data, rather than throw an exception, when
                        reading an ENDF file
  --skipCovariances     skip the covariance, if present
  --verboseWarnings     print verbose warnings
  --printBadNK14        print bad NK

### Shell script to run FUDGE translation script

In [26]:
import stat

translateSingleProtare = [
    '#!/usr/env/sh bash',
    '',
    'if [[ "$1" == "" ]]; then',
    '  echo "USAGE ERROR: $0 endf_file"',
    '  exit 1',
    'fi',
    '',
    'endf6File=$1',
    'gndsFile=$(basename ${endf6File}).gnds.xml',
    'logFile=${gndsFile%gnds.xml}log',
    'outputFile=${gndsFile%gnds.xml}out',
    f'python3 {translationScript} $endf6File $gndsFile --verbose 2>$logFile 1>$outputFile',
    ''
]

endf2gndsScript = pathlib.Path('endf2gnds.sh')
endf2gndsScript.write_text('\n'.join(translateSingleProtare))
endf2gndsScript.chmod(endf2gndsScript.stat().st_mode | stat.S_IEXEC)

### Translate files

In [ ]:
import tarfile as tarfileModule

projectileKeyMap = {"a": "alpha", "d": "deuteron", "g": "gamma", "h": "helion", "n": "neutron", "p": "proton", "t": "triton"}

for tarFile in pathlib.Path().glob('*.tgz'):
  projectileDir = tarFile.parent / projectileKeyMap[tarFile.name[-5]]
  if not projectileDir.is_dir():
    projectileDir.mkdir()
    tarfileModule.open(tarFile).extractall(path=projectileDir)

  gndsDir = projectileDir / 'gnds'
  if not gndsDir.is_dir():
    gndsDir.mkdir()

    fileList = [file.resolve() for file in projectileDir.glob('*.tendl')]
    numberFiles = len(fileList)
    for i, endf6File in enumerate(fileList):
      shellCommand = ['bash', endf2gndsScript.resolve(), endf6File]
      runShellCommand(shellCommand, gndsDir)
  
      if i % 10 == 0:
        print(f'{i}/{numberFiles} for {projectileKeyMap[tarFile.name[-5]]}s')

# TENDL-2021 library translation at LLNL 

### Summary of translation failures

The table below gives an overview of the number of translation failures for different versions of the FUDGE brownies module and command line arguments. The first column shows the version of FUDGE used for the translations. Version 6.2 was used in the first three cases with the arguments shown in the second column. The FUDGE/Brownies module was subsequently modified to ignore the problems associated with MF 8, 10 and 40. These are associated with radioactive production cross sections but they are redundant and are not necessary for transport applications. The resulting translations are shown in the last two cases below. 

| FUDGE Version             | Translation Script Arguments                    | alphas | deuterons | gammas | helions | neutrons | protons | tritons |
| --------------            | ----------------------------------------------- | ------ | --------- | ------ | ------- | -------- | ------- | ------- |
| 6.2                       | No Arguments                                    | 194    | 237       | 71     | 232     | 306      | 217     | 269     |
| 6.2                       | --acceptBadMF10FissionZAP                       | 194    | 236       | 71     | 232     | 306      | 217     | 269     |
| 6.2                       | --continuumSpectraFix                           | 194    | 236       | 71     | 232     | 245      | 216     | 269     |
| 6.2 with Brownies updates | No Arguments                                    | 2      | 2         | 0      | 2       | 84       | 4       | 1       |
| 6.2 with Brownies updates | --acceptBadMF10FissionZAP --continuumSpectraFix | 2      | 2         | 0      | 2       | 23       | 3       | 1       |

The remaining cases that failed to translate are the following:

- $^1H$ projectile: $^2H$, $^{237}Pa$ and $^{238}Pa$ targets

- $^2H$ projectile: $^3H$ and $^{237}U$ targets

- $^3H$ projectile: $^{236}U$ targets

- $^3He$ projectile: $^{236}Pa$ and $^{236}Th$ targets

- $^4He$ projectile: $^{233}Pa$ and $^{233}Th$ targets

- $n$ projectiles:

  - $^{2}H$
  - $^{241}Am$
  - $^{10}B$  
  - $^{9}Be$  
  - $^{243}Cm$
  - $^{262}Db$, $^{263}Db$, $^{264}Db$
  - $^{233}Pa$
  - $^{237}Pu$, $^{238}Pu$, $^{239}Pu$, $^{240}Pu$
  - $^{272}Sg$, $^{273}Sg$
  - $^{232}Th$
  - $^{232}U$, $^{234}U$, $^{235}U$, $^{236}U$, $^{237}U$, $^{239}U$, $^{240}U$